# Segmenting and Clustering Neighborhoods in Toronto

This notebook is intended for Capstone project week 3. 
In this assignment, we will explore, segment, and cluster the neighborhoods in the city of Toronto. We will collect the data from foursquare , make it in a structured format. Once the data is in a structured format, we will replicate the analysis that we did to the New York City dataset to explore and cluster the neighborhoods in the city of Toronto.

Before we download the data and start exploring it, let's download some dependencies needed by this notebook

In [0]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

/bin/bash: conda: command not found
Libraries imported.


## 1. Download and Explore Dataset

### 1.1. Prepare dataset when Toronto_Neighbourhood_Coordinate.csv is available in github account 'MariaTriagni'

If the Toronto_Neighbourhood_Coordinate.csv is available in github account 'MariaTriagni' ( https://github.com/MariaTriagni/Data/blob/master/Toronto_Neighbourhood_Coordinates.csv ) then all we need to do is just upload to dataframe

In [0]:
#If Toronto_Neighbourhood_Coordinate is exists already and it's available in github, load the csv from github to dataframe df_Toronto
if ( (isTorontoNeighbourghoodCoordFileExists == True) and (isReadCsvFromGithub == True)) :
  import pandas as pd 

  url = "https://raw.githubusercontent.com/MariaTriagni/Data/master/" + torontoNeighbourghoodCoordFile
  print(url)
  df_Toronto = pd.read_csv(url) 

df_Toronto.head() 


https://raw.githubusercontent.com/MariaTriagni/Data/master/Toronto_Neighbourhood_Coordinates.csv


Postcode          Borough     Neighbourhood   latitude  longitude
0      M5R  Central Toronto         Yorkville  43.671386 -79.390168
1      M3J       North York   York University  43.779242 -79.483559
2      M2P       North York   York Mills West  43.744039 -79.406657
3      M2L       North York        York Mills  43.744039 -79.406657
4      M4C        East York  Woodbine Heights  43.699930 -79.319132

In [0]:
df_Toronto

Postcode           Borough     Neighbourhood   latitude  longitude
0        M5R   Central Toronto         Yorkville  43.671386 -79.390168
1        M3J        North York   York University  43.779242 -79.483559
2        M2P        North York   York Mills West  43.744039 -79.406657
3        M2L        North York        York Mills  43.744039 -79.406657
4        M4C         East York  Woodbine Heights  43.699930 -79.319132
..       ...               ...               ...        ...        ...
282      M8W         Etobicoke         Alderwood  43.601717 -79.545232
283      M9V         Etobicoke    Albion Gardens  43.741665 -79.584543
284      M1V       Scarborough   Agincourt North  43.808038 -79.266439
285      M1S       Scarborough         Agincourt  43.785353 -79.278549
286      M5H  Downtown Toronto          Adelaide  43.650823 -79.377936

[287 rows x 5 columns]

### 1.2. Clean the dataset

In the dataset, we can see some neighbourhood doesn't have latitude and longitude and some postal code also doesn't have latitude and longitude. We will remove all the neighbourhood which doesn't have latitude and longitude.

In [0]:
#get the index list of the dataframe
#list(df_Toronto.index) 

In [0]:
# Get the list of indexes for which column latitude or longitude has value 0.0
indexNames = df_Toronto[ (df_Toronto['latitude'] == 0.0) | (df_Toronto['longitude'] == 0.0) ].index
 
# View the list of indexes indexNames
indexNames

Int64Index([ 45,  74,  87,  88,  89,  90,  91,  92,  93,  94,  95,  96,  97,
             98,  99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110,
            111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123,
            124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136,
            137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149,
            150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162,
            163, 164, 209, 213, 251, 266, 267, 269, 270, 272, 278],
           dtype='int64')

In [0]:
# Delete these row indexes from dataFrame
df_Toronto.drop(indexNames , inplace=True)
df_Toronto

Postcode           Borough     Neighbourhood   latitude  longitude
0        M5R   Central Toronto         Yorkville  43.671386 -79.390168
1        M3J        North York   York University  43.779242 -79.483559
2        M2P        North York   York Mills West  43.744039 -79.406657
3        M2L        North York        York Mills  43.744039 -79.406657
4        M4C         East York  Woodbine Heights  43.699930 -79.319132
..       ...               ...               ...        ...        ...
282      M8W         Etobicoke         Alderwood  43.601717 -79.545232
283      M9V         Etobicoke    Albion Gardens  43.741665 -79.584543
284      M1V       Scarborough   Agincourt North  43.808038 -79.266439
285      M1S       Scarborough         Agincourt  43.785353 -79.278549
286      M5H  Downtown Toronto          Adelaide  43.650823 -79.377936

[198 rows x 5 columns]

Now dataframe df_Toronto has clean data and ready for next step

## 2. Analyze the data set

In this section, we will use the Foursquare API to explore neighborhoods in Toronto city. We will use the explore function to get the most common venue categories in each neighborhood, and then use this feature to group the neighborhoods into clusters. We will use the k-means clustering algorithm to complete this task. Finally, we will use the Folium library to visualize the neighborhoods in Toronto city.

## 2.1 Create a map of Toronto with neighborhoods superimposed on top.

#### Use geopy library to get the latitude and longitude values of Toronto City.

In [0]:
address = 'Toronto City, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto City are 43.653963, -79.387207.


In [0]:
# create map of Toronto using latitude and longitude values
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_Toronto['latitude'], df_Toronto['longitude'], df_Toronto['Borough'], df_Toronto['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto)  
    
map_Toronto

#### Define Foursquare Credentials and Version

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

In [0]:
CLIENT_ID = 'JDM0SDUZFOHLIGWTRF0NG0CEP3E3WFX1B1YQCTXISRS155ZX' # your Foursquare ID
CLIENT_SECRET = 'O0WTBPZXI5FUWPESAH01PJIZF4BW023A1YKGVPAX5RK5WCYO' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: JDM0SDUZFOHLIGWTRF0NG0CEP3E3WFX1B1YQCTXISRS155ZX
CLIENT_SECRET:O0WTBPZXI5FUWPESAH01PJIZF4BW023A1YKGVPAX5RK5WCYO


#### Let's create a function to get venues to all the neighborhoods in Toronto

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT = 100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        json_response = requests.get(url).json()
        #print(type(json_response["response"]['groups']))
        results = json_response["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Now run the getNearbyVenues function to all neighbourhood in Toronto city

In [0]:
toronto_venues = getNearbyVenues(names=df_Toronto['Neighbourhood'],
                                   latitudes=df_Toronto['latitude'],
                                   longitudes=df_Toronto['longitude']
                                  )

print('finish')

Yorkville
<class 'list'>
York University
<class 'list'>
York Mills West
<class 'list'>
York Mills
<class 'list'>
Woodbine Heights
<class 'list'>
Woodbine Gardens
<class 'list'>
Woburn
<class 'list'>
Wilson Heights
<class 'list'>
Willowdale West
<class 'list'>
Willowdale South
<class 'list'>
Willowdale
<class 'list'>
Wexford Heights
<class 'list'>
Wexford
<class 'list'>
Weston
<class 'list'>
Westmount
<class 'list'>
West Hill
<class 'list'>
West Deane Park
<class 'list'>
Victoria Village
<class 'list'>
Victoria Hotel
<class 'list'>
Upwood Park
<class 'list'>
Upper Rouge
<class 'list'>
University of Toronto
<class 'list'>
Union Station
<class 'list'>
Underground city
<class 'list'>
Trinity
<class 'list'>
Toronto Islands
<class 'list'>
Toronto Dominion Centre
<class 'list'>
Thorncliffe Park
<class 'list'>
Thistletown
<class 'list'>
The Queensway West
<class 'list'>
The Queensway East
<class 'list'>
The Kingsway
<class 'list'>
The Junction South
<class 'list'>
The Junction North
<class 'li

#### Let's check the size of the resulting dataframe

In [0]:
print(toronto_venues.shape)
toronto_venues.head()

(5975, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Yorkville              43.671386              -79.390168   
1    Yorkville              43.671386              -79.390168   
2    Yorkville              43.671386              -79.390168   
3    Yorkville              43.671386              -79.390168   
4    Yorkville              43.671386              -79.390168   

                         Venue  Venue Latitude  Venue Longitude  \
0         Paramount Fine Foods       43.670677       -79.389865   
1   Four Seasons Hotel Toronto       43.671796       -79.389457   
2                       Pi Co.       43.670107       -79.389852   
3  Summer's Homemade Ice Cream       43.670903       -79.392299   
4                       Eataly       43.669754       -79.388720   

              Venue Category  
0  Middle Eastern Restaurant  
1                      Hotel  
2                Pizza Place  
3             Ice Cream Shop  
4               Gourmet Shop

Let's check how many venues were returned for each neighborhood

In [0]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                              
Adelaide                                    100                     100   
Agincourt                                    12                      12   
Agincourt North                              27                      27   
Albion Gardens                               12                      12   
Alderwood                                     9                       9   
Bathurst Manor                                5                       5   
Bathurst Quay                                24                      24   
Bayview Village                              12                      12   
Bedford Park                                  2                       2   
Berczy Park                                 100                     100   
Birch Cliff                                   4                       4   
Bloordale Gardens                             9                       9   
Brockton                                     19                      19   
CN Tower                                     92                      92   
Cabbagetown                                  53                      53   
Cedarbrae                                    23                      23   
Chinatown                                    91                      91   
Christie                                     58                      58   
Church and Wellesley                         86                      86   
Clairlea                                     10                      10   
Clarks Corners                                4                       4   
Cliffcrest                                    7                       7   
Cliffside                                     7                       7   
Cliffside West                                7                       7   
Cloverdale                                   23                      23   
Commerce Court                              100                     100   
Davisville                                   44                      44   
Davisville North                             44                      44   
Deer Park                                    54                      54   
Design Exchange                             100                     100   
Don Mills North                              69                      69   
Don Mills South                              69                      69   
Dorset Park                                  11                      11   
Dovercourt Village                            9                       9   
Downsview                                     9                       9   
Downsview Central                             9                       9   
Downsview East                                9                       9   
Downsview North                               9                       9   
Downsview Northwest                           9                       9   
Downsview West                                9                       9   
Dufferin                                     43                      43   
East Birchmount Park                          4                       4   
East Toronto                                  1                       1   
Emery                                         9                       9   
Eringate                                      2                       2   
Exhibition Place                             37                      37   
Fairview                                     79                      79   
First Canadian Place                        100                     100   
Flemingdon Park                              14                      14   
Forest Hill North                             4                       4   
Forest Hill SE                                4                       4   
Forest Hill West                             21    

#### Let's find out how many unique categories can be curated from all the returned venues

In [0]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 338 uniques categories.


## 3. Analyze Each Neighborhood

In [0]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
#fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
#toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()


ATM  Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0    0                  0                  0                   0        0   
1    0                  0                  0                   0        0   
2    0                  0                  0                   0        0   
3    0                  0                  0                   0        0   
4    0                  0                  0                   0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Argentinian Restaurant  \
0                    0             0         0                       0   
1                    0             0         0                       0   
2                    0             0         0                       0   
3                    0             0         0                       0   
4                    0             0         0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  Automotive Shop  \
0                 0                   0                0                0   
1                 0                   0                0                0   
2                 0                   0                0                0   
3                 0                   0                0                0   
4                 0                   0                0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0          0           0       0     0    0               0                 0   
1          0           0       0     0    0               0                 0   
2          0           0       0     0    0               0                 0   
3          0           0       0     0    0               0                 0   
4          0           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Beach Bar  Bed & Breakfast  Beer Bar  \
0                   0      0          0                0         0   
1                   0      0          0                0         0   
2                   0      0          0                0         0   
3                   0      0          0                0         0   
4                   0      0          0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Big Box Store  Bike Shop  \
0            0           0                   0              0          0   
1            0           0                   0              0          0   
2            0           0                   0              0          0   
3            0           0                   0              0          0   
4            0           0                   0              0          0   

   Bike Trail  Bistro  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0           0       0              0          0         0              0   
1           0       0              0          0         0              0   
2           0       0              0          0         0              0   
3           0       0              0          0         0          

And let's examine the new dataframe size.

In [0]:
toronto_onehot.shape

(5975, 338)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [0]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood       ATM  Accessories Store  Afghan Restaurant  \
0                    Adelaide  0.000000           0.000000           0.000000   
1                   Agincourt  0.000000           0.000000           0.000000   
2             Agincourt North  0.000000           0.000000           0.000000   
3              Albion Gardens  0.000000           0.000000           0.000000   
4                   Alderwood  0.000000           0.000000           0.000000   
5              Bathurst Manor  0.000000           0.000000           0.000000   
6               Bathurst Quay  0.000000           0.000000           0.000000   
7             Bayview Village  0.000000           0.000000           0.000000   
8                Bedford Park  0.000000           0.000000           0.000000   
9                 Berczy Park  0.000000           0.000000           0.000000   
10                Birch Cliff  0.000000           0.000000           0.000000   
11          Bloordale Gardens  0.000000           0.000000           0.000000   
12                   Brockton  0.000000           0.000000           0.000000   
13                   CN Tower  0.000000           0.000000           0.000000   
14                Cabbagetown  0.000000           0.000000           0.000000   
15                  Cedarbrae  0.000000           0.000000           0.000000   
16                  Chinatown  0.000000           0.000000           0.000000   
17                   Christie  0.000000           0.000000           0.000000   
18       Church and Wellesley  0.000000           0.000000           0.011628   
19                   Clairlea  0.000000           0.000000           0.000000   
20             Clarks Corners  0.000000           0.000000           0.000000   
21                 Cliffcrest  0.000000           0.000000           0.000000   
22                  Cliffside  0.000000           0.000000           0.000000   
23             Cliffside West  0.000000           0.000000           0.000000   
24                 Cloverdale  0.000000           0.000000           0.000000   
25             Commerce Court  0.000000           0.000000           0.000000   
26                 Davisville  0.000000           0.000000           0.000000   
27           Davisville North  0.000000           0.000000           0.000000   
28                  Deer Park  0.000000           0.000000           0.000000   
29            Design Exchange  0.000000           0.000000           0.000000   
30            Don Mills North  0.000000           0.000000           0.000000   
31            Don Mills South  0.000000           0.000000           0.000000   
32                Dorset Park  0.000000           0.090909           0.000000   
33         Dovercourt Village  0.000000           0.000000           0.000000   
34                  Downsview  0.000000           0.000000           0.000000   
35          Downsview Central  0.000000           0.000000           0.000000   
36             Downsview East  0.000000           0.000000           0.000000   
37            Downsview North  0.000000           0.000000           0.000000   
38        Downsview Northwest  0.000000           0.000000           0.000000   
39             Downsview West  0.000000           0.000000           0.000000   
40                   Dufferin  0.000000           0.000000           0.000000   
41       East Birchmount Park  0.000000           0.000000           0.000000   
42               East Toronto  0.000000           0.000000           0.000000   
43                      Emery  0.000000           0.000000           0.000000   
44                   Eringate  0.000000           0.000000           0.000000   
45           Exhibition Place  0.000000           0.000000           0.000000   
46                   Fairview  0.000000           0.000000           0.000000   
47       First Canadian Place  0.000000           0.000000           0.000000   
48            Flemingdon Park  0.000000         

Let's confirm the new size

In [0]:
toronto_grouped.shape

(195, 338)

#### Let's print each neighborhood along with the top 5 most common venues

In [0]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
            venue  freq
0     Coffee Shop  0.08
1      Restaurant  0.06
2            Café  0.05
3       Gastropub  0.04
4  Cosmetics Shop  0.04


----Agincourt----
                   venue  freq
0     Chinese Restaurant  0.25
1   Hong Kong Restaurant  0.08
2            Coffee Shop  0.08
3          Shopping Mall  0.08
4  Vietnamese Restaurant  0.08


----Agincourt North----
                  venue  freq
0    Chinese Restaurant  0.07
1                Bakery  0.07
2            Taco Place  0.04
3                  Bank  0.04
4  Fast Food Restaurant  0.04


----Albion Gardens----
                 venue  freq
0        Grocery Store  0.17
1             Pharmacy  0.08
2  Fried Chicken Joint  0.08
3  Japanese Restaurant  0.08
4       Hardware Store  0.08


----Alderwood----
            venue  freq
0     Pizza Place  0.22
1            Pool  0.11
2    Skating Rink  0.11
3     Coffee Shop  0.11
4  Sandwich Place  0.11


----Bathurst Manor----
               venue  freq
0         Ba

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [0]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [0]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide           Coffee Shop            Restaurant   
1        Agincourt    Chinese Restaurant         Train Station   
2  Agincourt North    Chinese Restaurant                Bakery   
3   Albion Gardens         Grocery Store   Fried Chicken Joint   
4        Alderwood           Pizza Place                  Pool   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0                  Café             Gastropub         Cosmetics Shop   
1  Cantonese Restaurant  Hong Kong Restaurant  Vietnamese Restaurant   
2                   Spa   Japanese Restaurant    Fried Chicken Joint   
3              Pharmacy  Caribbean Restaurant         Sandwich Place   
4                   Pub                   Gym         Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0   American Restaurant        Breakfast Spot                 Hotel   
1     Korean Restaurant      Asian Restaurant           Coffee Shop   
2         Movie Theater    Frozen Yogurt Shop   Sporting Goods Shop   
3        Hardware Store            Beer Store   Japanese Restaurant   
4              Pharmacy          Skating Rink           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0    Italian Restaurant         Clothing Store  
1         Shopping Mall    Rental Car Location  
2  Fast Food Restaurant             Beer Store  
3  Fast Food Restaurant            Video Store  
4               Exhibit      Electronics Store

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [0]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 2, 0, 0, 1, 0], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [0]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_Toronto
toronto_merged.rename(columns={"Neighbourhood": "Neighborhood"}, inplace = True )

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Postcode          Borough      Neighborhood   latitude  longitude  \
0      M5R  Central Toronto         Yorkville  43.671386 -79.390168   
1      M3J       North York   York University  43.779242 -79.483559   
2      M2P       North York   York Mills West  43.744039 -79.406657   
3      M2L       North York        York Mills  43.744039 -79.406657   
4      M4C        East York  Woodbine Heights  43.699930 -79.319132   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             0.0                  Café              Boutique   
1             0.0           Gas Station      Business Service   
2             0.0           Coffee Shop            Restaurant   
3             0.0           Coffee Shop            Restaurant   
4             0.0          Skating Rink              Bus Stop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Italian Restaurant           Coffee Shop                 Hotel   
1           Yoga Studio              Festival  Ethiopian Restaurant   
2      Business Service         Burrito Place                  Park   
3      Business Service         Burrito Place                  Park   
4        Cosmetics Shop          Dance Studio    Athletics & Sports   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Restaurant                   Spa     French Restaurant   
1           Event Space               Exhibit    Falafel Restaurant   
2  Gym / Fitness Center                   Gym   Japanese Restaurant   
3  Gym / Fitness Center                   Gym   Japanese Restaurant   
4              Pharmacy                  Park           Yoga Studio   

  9th Most Common Venue 10th Most Common Venue  
0        Clothing Store          Women's Store  
1                  Farm         Farmers Market  
2                   Pub        Thai Restaurant  
3                   Pub        Thai Restaurant  
4           Event Space                Exhibit

Finally, let's visualize the resulting clusters

In [0]:
import math

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['latitude'], toronto_merged['longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    if (math.isnan(cluster)):
      cluster = 0
      print('nan')
    cluster_int = int(cluster)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster_int-1],
        fill=True,
        fill_color=rainbow[cluster_int-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

nan


## 5. Examine Clusters

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

#### Cluster 1

In [0]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough              Neighborhood  Cluster Labels  \
0     Central Toronto                 Yorkville             0.0   
1          North York           York University             0.0   
2          North York           York Mills West             0.0   
3          North York                York Mills             0.0   
4           East York          Woodbine Heights             0.0   
5           East York          Woodbine Gardens             0.0   
6         Scarborough                    Woburn             0.0   
7          North York            Wilson Heights             0.0   
8          North York           Willowdale West             0.0   
9          North York          Willowdale South             0.0   
10         North York                Willowdale             0.0   
11        Scarborough           Wexford Heights             0.0   
12        Scarborough                   Wexford             0.0   
13               York                    Weston             0.0   
15        Scarborough                 West Hill             0.0   
17         North York          Victoria Village             0.0   
18   Downtown Toronto            Victoria Hotel             0.0   
19         North York               Upwood Park             0.0   
21   Downtown Toronto     University of Toronto             0.0   
22   Downtown Toronto             Union Station             0.0   
23   Downtown Toronto          Underground city             0.0   
24       West Toronto                   Trinity             0.0   
25   Downtown Toronto           Toronto Islands             0.0   
26   Downtown Toronto   Toronto Dominion Centre             0.0   
27          East York          Thorncliffe Park             0.0   
28          Etobicoke               Thistletown             0.0   
29          Etobicoke        The Queensway West             0.0   
30          Etobicoke        The Queensway East             0.0   
31          Etobicoke              The Kingsway             0.0   
32       West Toronto        The Junction South             0.0   
33               York        The Junction North             0.0   
34       East Toronto         The Danforth West             0.0   
35       East Toronto          The Beaches West             0.0   
36       East Toronto               The Beaches             0.0   
37    Central Toronto                 The Annex             0.0   
38        Scarborough             Tam O'Shanter             0.0   
41    Central Toronto           Summerhill West             0.0   
42    Central Toronto           Summerhill East             0.0   
43        Scarborough                  Sullivan             0.0   
44       East Toronto           Studio District             0.0   
47          Etobicoke              St. Phillips             0.0   
48   Downtown Toronto            St. James Town             0.0   
49   Downtown Toronto            St. James Town             0.0   
51          Etobicoke            South of Bloor             0.0   
52   Downtown Toronto             South Niagara             0.0   
53    Central Toronto                South Hill             0.0   
54               York               Silverthorn             0.0   
55          Etobicoke               Silverstone             0.0   
57        Scarborough  Scarborough Village West             0.0   
58        Scarborough       Scarborough Village             0.0   
59        Scarborough   Scarborough Town Centre             0.0   
60   Downtown Toronto                   Ryerson             0.0   
61               York                 Runnymede             0.0   
62       West Toronto                 Runnymede             0.0   
63          Etobicoke     Royal York South West             0.0   
64          Etobicoke     Royal York South East             0.0   
65        Scarborough                Rouge Hill             0.0   
67    Central Toronto                  Roselawn             0.0   
69       West Toronto              Roncesvalles             0

#### Cluster 2

In [0]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough   Neighborhood  Cluster Labels       1st Most Common Venue  \
40    Etobicoke       Sunnylea             1.0               Poutine Place   
79    East York  Parkview Hill             1.0  Construction & Landscaping   
214   Etobicoke     Humber Bay             1.0                        Park   
235   Etobicoke       Eringate             1.0                        Park   
277  North York   Bedford Park             1.0  Construction & Landscaping   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
40   Construction & Landscaping           Art Gallery           Yoga Studio   
79                  Yoga Studio   Filipino Restaurant  Ethiopian Restaurant   
214  Construction & Landscaping       Harbor / Marina          Home Service   
235  Construction & Landscaping           Yoga Studio  Fast Food Restaurant   
277         Rental Car Location           Yoga Studio              Festival   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
40   Fast Food Restaurant   Empanada Restaurant  Ethiopian Restaurant   
79            Event Space               Exhibit    Falafel Restaurant   
214           Yoga Studio        Farmers Market   Empanada Restaurant   
235   Empanada Restaurant  Ethiopian Restaurant           Event Space   
277   Empanada Restaurant  Ethiopian Restaurant           Event Space   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
40            Event Space               Exhibit     Falafel Restaurant  
79                   Farm        Farmers Market   Fast Food Restaurant  
214  Ethiopian Restaurant           Event Space                Exhibit  
235               Exhibit    Falafel Restaurant                   Farm  
277               Exhibit    Falafel Restaurant                   Farm

#### Cluster 3

In [0]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough              Neighborhood  Cluster Labels  \
14          Etobicoke                 Westmount             2.0   
20        Scarborough               Upper Rouge             2.0   
39       West Toronto                   Swansea             2.0   
56         North York              Silver Hills             2.0   
66        Scarborough                     Rouge             2.0   
68   Downtown Toronto                  Rosedale             2.0   
72   Downtown Toronto                  Richmond             2.0   
83          Etobicoke            Old Mill South             2.0   
84          Etobicoke            Old Mill North             2.0   
85          Etobicoke         Old Burnhamthorpe             2.0   
165        North York            Northwood Park             2.0   
175   Central Toronto                Moore Park             2.0   
184         Etobicoke             Markland Wood             2.0   
188         East York                   Leaside             2.0   
190        North York       Lawrence Manor East             2.0   
191        North York            Lawrence Manor             2.0   
195         Etobicoke  Kingsway Park South West             2.0   
196         Etobicoke  Kingsway Park South East             2.0   
198         Etobicoke          King's Mill Park             2.0   
207       Scarborough                   Ionview             2.0   
212        North York             Humber Summit             2.0   
218        North York                Henry Farm             2.0   
229   Central Toronto            Forest Hill SE             2.0   
230   Central Toronto         Forest Hill North             2.0   
261       Scarborough            Clarks Corners             2.0   
275       Scarborough               Birch Cliff             2.0   
281        North York            Bathurst Manor             2.0   

         1st Most Common Venue       2nd Most Common Venue  \
14                        Park                 Pizza Place   
20                        Park        Fast Food Restaurant   
39                 Social Club  Construction & Landscaping   
56   Middle Eastern Restaurant                        Park   
66                        Park        Fast Food Restaurant   
68                        Park                  Playground   
72                        Park                  Beer Store   
83                        Park                       River   
84                        Park                       River   
85                     Dog Run                 Flower Shop   
165                       Park              Baseball Field   
175                 Playground                       Trail   
184                Golf Course              Baseball Field   
188          Convenience Store              Sandwich Place   
190          Electronics Store                        Bank   
191          Electronics Store                        Bank   
195                  Jazz Club               Metro Station   
196                  Jazz Club               Metro Station   
198                       Park                  Playground   
207              Metro Station               Deli / Bodega   
212                     Bakery         Empanada Restaurant   
218                 Restaurant                Tennis Court   
229                       Bank                  Playground   
230                       Bank                  Playground   
261       Caribbean Restaurant           Convenience Store   
275                   Gym Pool            Business Service   
281                 Bagel Shop                  Playground   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
14                  Gas Station           Yoga Studio  Fast Food Restaurant   
20                  Yoga Studio              Festival  Ethiopian Restaurant   
39               Pilates Studio          Skating Rink                  Park   
56                  Yoga Studio              Festival  Ethiopian Restaurant   
66   

#### Cluster 4

In [0]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough       Neighborhood  Cluster Labels 1st Most Common Venue  \
77   Scarborough         Port Union             3.0                  Park   
197    Etobicoke  Kingsview Village             3.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
77            Yoga Studio              Festival  Ethiopian Restaurant   
197           Yoga Studio              Festival  Ethiopian Restaurant   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
77            Event Space               Exhibit    Falafel Restaurant   
197           Event Space               Exhibit    Falafel Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
77                   Farm        Farmers Market   Fast Food Restaurant  
197                  Farm        Farmers Market   Fast Food Restaurant

#### Cluster 5

In [0]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + [2] + list(range(5, toronto_merged.shape[1]))]]

Borough   Neighborhood  Cluster Labels 1st Most Common Venue  \
46  Scarborough   Steeles East             4.0            Playground   
50    Etobicoke  South Steeles             4.0            Playground   

      2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
46  Health & Beauty Service           Yoga Studio  Fast Food Restaurant   
50  Health & Beauty Service           Yoga Studio  Fast Food Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
46   Empanada Restaurant  Ethiopian Restaurant           Event Space   
50   Empanada Restaurant  Ethiopian Restaurant           Event Space   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
46               Exhibit    Falafel Restaurant                   Farm  
50               Exhibit    Falafel Restaurant                   Farm